In [1]:
import sys
import time
from io import BytesIO
import pandas as pd
import numpy as np
import requests 
from bs4 import BeautifulSoup

import time
from time import sleep

import concurrent.futures

In [2]:
df = pd.read_csv (r'resultCity.csv')
df.drop("Unnamed: 0",axis='columns', inplace=True)
df

Country    District               City  \
0      Afghanistan  Badakhshan  Kuran wa Munjan38   
1      Afghanistan  Badakhshan  Bazar-e Tashkan34   
2      Afghanistan  Badakhshan          Darayim34   
3      Afghanistan  Badakhshan      Deh Khwahan34   
4      Afghanistan  Badakhshan         Fayzabad34   
...            ...         ...                ...   
58659     Zimbabwe    Midlands            Gweru25   
58660     Zimbabwe    Midlands        Lalapanzi25   
58661     Zimbabwe    Midlands            Mvuma25   
58662     Zimbabwe    Midlands         Shangani25   
58663     Zimbabwe    Midlands         Shurugwi25   

                                            Link to city  
0      https://www.iqair.com/afghanistan/badakhshan/k...  
1      https://www.iqair.com/afghanistan/badakhshan/b...  
2      https://www.iqair.com/afghanistan/badakhshan/d...  
3      https://www.iqair.com/afghanistan/badakhshan/d...  
4      https://www.iqair.com/afghanistan/badakhshan/f...  
...                                                  ...  
58659      https://www.iqair.com/zimbabwe/midlands/gweru  
58660  https://www.iqair.com/zimbabwe/midlands/lalapanzi  
58661      https://www.iqair.com/zimbabwe/midlands/mvuma  
58662   https://www.iqair.com/zimbabwe/midlands/shangani  
58663   https://www.iqair.com/zimbabwe/midlands/shurugwi  

[58664 rows x 4 columns]

In [3]:
link_to_city=list()
for link in df["Link to city"]:
    link_to_city.append(link)

In [4]:
cities=list()
for city in df["City"]:
    city=city.replace("," ," ")
    city = ''.join([i for i in city if not i.isdigit()])
    cities.append(city)
len(cities)

58664

In [5]:
states=list()
for state in df["District"]:
    state=state.replace("," ,"")
    states.append(state)

In [6]:
countries=list()
for country in df["Country"]:
    country=country.replace("," ,"")
    countries.append(country)  

In [ ]:
def web_scrape(url,city,state,country):
    headers = {"user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/88.0.4324.190 Safari/537.36"}
    response = requests.get(url, headers=headers)
    
    if (response.status_code == 200):
        soup = BeautifulSoup(response.content, "html.parser")
        try:
            gtag=soup.find("div",attrs={"class":"aqi-overview__summary"})
            aqi=gtag.find("p", attrs={"class":"aqi-value__value"}).get_text().strip(" *")    
            wtag=soup.find("tbody")
            temp=wtag.findAll("td")[3].get_text().strip("°C")
            hum=wtag.findAll("td")[5].get_text().strip("%")
            wind=wtag.findAll("td")[7].get_text().strip(" mp/h")
            pressure=wtag.findAll("td")[9].get_text().strip(" mb")
            return aqi,temp,hum,wind,pressure,url,city,state,country
        except:
            pass
    response.close()
    if (response.status_code != 200):
        print("Could not reach: {} status code: {} ".format(response.url, response.status_code))
        time.sleep(10)    

            
with concurrent.futures.ThreadPoolExecutor(max_workers=15) as executor:
    futures = []
    for link,city,state,country in zip(link_to_city,cities,states,countries):
        futures.append(executor.submit(web_scrape, url=link,city=city,state=state,country=country))
    result=list()
    try:
        for future in concurrent.futures.as_completed(futures):
            try: 
                result.append(future.result(timeout=2))
                print (future.result(timeout=2))
            except: 
                pass
    except Exception as e:
        print(e)
              
print("Threaded time:", time.time())
   
      

('55', '30', '18', '14.3', '1007', 'https://www.iqair.com/afghanistan/badakhshan/darayim', 'Darayim', 'Badakhshan', 'Afghanistan')
('55', '36', '15', '12.2', '1005', 'https://www.iqair.com/afghanistan/badakhshan/mashhad', 'Mashhad', 'Badakhshan', 'Afghanistan')
('55', '33', '16', '11.2', '1005', 'https://www.iqair.com/afghanistan/badakhshan/bazar-e-tashkan', 'Bazar-e Tashkan', 'Badakhshan', 'Afghanistan')
('53', '18', '44', '6.9', '1015', 'https://www.iqair.com/afghanistan/badakhshan/kuran-wa-munjan', 'Kuran wa Munjan', 'Badakhshan', 'Afghanistan')
('57', '35', '18', '10.8', '1006', 'https://www.iqair.com/afghanistan/badakhshan/deh-khwahan', 'Deh Khwahan', 'Badakhshan', 'Afghanistan')
('55', '33', '18', '11.3', '1006', 'https://www.iqair.com/afghanistan/badakhshan/fayzabad', 'Fayzabad', 'Badakhshan', 'Afghanistan')
('51', '17', '33', '12', '1013', 'https://www.iqair.com/afghanistan/badakhshan/ashkasham', 'Ashkasham', 'Badakhshan', 'Afghanistan')
('53', '25', '29', '9.6', '1011', 'https

In [12]:
df_City=pd.DataFrame({"data":result})
df_City.to_csv("result_ex.csv")